# Graph Server (PGX) und Vis.JS

## First Step: Install Oracle Database and Graph libraries

In [24]:
!pip install oracledb oracle-graph-client install-jdk pyvis

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 756.0/756.0 kB 2.5 MB/s eta 0:00:00:00:010:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.2/46.2 kB 16.9 MB/s eta 0:00:00
17:00:54.339 [idle-connection-evictor-1] DEBUG org.apache.hc.client5.http.impl.io.PoolingHttpClientConnectionManager -- Closing expired connections
17:00:54.339 [idle-connection-evictor-1] DEBUG org.apache.hc.client5.http.impl.io.PoolingHttpClientConnectionManager -- Closing connections idle longer than 1 MINUTES


## Install JDK 17 into Jupyter container

In [4]:
import jdk
import os
from jdk.enums import OperatingSystem, Architecture

javapath = jdk.install('17', operating_system=OperatingSystem.LINUX)
os.environ['JAVA_HOME'] = javapath
os.environ['PATH'] = f"{os.environ.get('PATH')}:{os.environ.get('JAVA_HOME')}/bin"

In [39]:
print (javapath)

/home/jovyan/.jdk/jdk-17.0.13+11


## set user name, password and URL to graph server

In [3]:
import json
import os
import getpass
#user = 'BANKGRAPH'
username = input('Enter database username: ')
password = getpass.getpass('Enter Password for ' + username + ' user: ')

baseUrl = os.environ.get('GRAPH_URL')
print (baseUrl)

Enter database username:  bankgraph
Enter Password for bankgraph user:  ········


http://graphtest-graph-server-svc:7007


## Connect to Graph Server (PGX)

In [41]:
import pypgx as pgx
from opg4py import graph_server
instance = graph_server.get_instance(baseUrl, username, password)
session = instance.create_session("pypgx_example_session")
print(session)

16:11:34.544 [main] INFO oracle.pg.rdbms.internal.AbstractHttpClient -- POST http://graph-server.graph-oradb:7007/auth/token
16:11:34.558 [main] DEBUG org.apache.hc.client5.http.impl.classic.InternalHttpClient -- ex-0000000166 preparing request execution
16:11:34.559 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000166 target auth state: UNCHALLENGED
16:11:34.559 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000166 proxy auth state: UNCHALLENGED
16:11:34.559 [main] DEBUG org.apache.hc.client5.http.impl.classic.ConnectExec -- ex-0000000166 acquiring connection with route {}->http://graph-server.graph-oradb:7007
16:11:34.559 [main] DEBUG org.apache.hc.client5.http.impl.classic.InternalHttpClient -- ex-0000000166 acquiring endpoint (3 MINUTES)
16:11:34.559 [main] DEBUG org.apache.hc.client5.http.impl.io.PoolingHttpClientConnectionManager -- ex-0000000166 endpoint lease request (3 MINUTES) [route: {}->http://graph-server.graph-ora

## Create a graph from scratch for testing

In [9]:

graph = session.create_graph_builder().add_edge(1, 2).add_edge(2, 3).add_edge(3, 1).build()
analyst = session.create_analyst()

triangles = analyst.count_triangles(graph, True)
print("triangles = {}".format(triangles))


16:33:05.085 [main] DEBUG oracle.pgx.api.GraphBuilderImpl -- Parsed Graph Builder Config: {"edge_id_generation_strategy":"AUTO_GENERATED","vertex_id_generation_strategy":"USER_IDS"}
16:33:05.394 [main] DEBUG oracle.pgx.client.RemoteUtils -- create session cookie (session ID = e17553f2-8e88-431f-bf79-bc4cc2264a79)
16:33:05.404 [main] DEBUG oracle.pgx.client.RemoteUtils -- no value for the sticky cookie given
16:33:05.413 [main] DEBUG oracle.pgx.client.RemoteUtils -- create csrf token cookie (token = 6a2fab4b-5143-4c09-8357-2a832489cf2c)
16:33:06.453 [main] DEBUG oracle.pgx.client.HttpRequestExecutor -- Requesting PATCH http://graph-server.graph-oradb:7007/core/v1/changes
16:33:06.453 [main] DEBUG org.apache.hc.client5.http.impl.classic.InternalHttpClient -- ex-0000000008 preparing request execution
16:33:06.454 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000008 target auth state: UNCHALLENGED
16:33:06.454 [main] DEBUG org.apache.hc.client5.http.impl.class

## Query that test graph

In [10]:
rs = graph.query_pgql("select x, y, e from match (x) -[e]-> (y)")
rs.print()

16:33:20.830 [main] DEBUG oracle.pgx.client.RemoteUtils -- create session cookie (session ID = e17553f2-8e88-431f-bf79-bc4cc2264a79)
16:33:20.830 [main] DEBUG oracle.pgx.client.RemoteUtils -- no value for the sticky cookie given
16:33:20.830 [main] DEBUG oracle.pgx.client.RemoteUtils -- create csrf token cookie (token = 6a2fab4b-5143-4c09-8357-2a832489cf2c)
16:33:20.832 [main] DEBUG oracle.pgx.client.HttpRequestExecutor -- Requesting POST http://graph-server.graph-oradb:7007/core/v1/pgql/run
16:33:20.833 [main] DEBUG org.apache.hc.client5.http.impl.classic.InternalHttpClient -- ex-0000000027 preparing request execution
16:33:20.833 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000027 target auth state: UNCHALLENGED
16:33:20.833 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000027 proxy auth state: UNCHALLENGED
16:33:20.833 [main] DEBUG org.apache.hc.client5.http.impl.classic.ConnectExec -- ex-0000000027 acquiring connection wi

## Now , read a more complex graph from the attached Oracle database into PGX

In [43]:
graph = session.read_graph_by_name('BANK_GRAPH', 'pg_sql')

# printing the graph shows how many nodes and edges it has.
print(graph)


16:12:49.289 [main] DEBUG oracle.pgx.client.RemoteUtils -- create session cookie (session ID = 27b7496d-4e94-43fb-8d2e-5dd1d8a4425d)
16:12:49.289 [main] DEBUG oracle.pgx.client.RemoteUtils -- no value for the sticky cookie given
16:12:49.289 [main] DEBUG oracle.pgx.client.RemoteUtils -- create csrf token cookie (token = 0ce1d5f5-989b-4999-948e-623fc4dede0a)
16:12:49.297 [main] DEBUG oracle.pgx.client.HttpRequestExecutor -- Requesting POST http://graph-server.graph-oradb:7007/core/v2/describe
16:12:49.297 [main] DEBUG org.apache.hc.client5.http.impl.classic.InternalHttpClient -- ex-0000000175 preparing request execution
16:12:49.297 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000175 target auth state: UNCHALLENGED
16:12:49.297 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000175 proxy auth state: UNCHALLENGED
16:12:49.297 [main] DEBUG org.apache.hc.client5.http.impl.classic.ConnectExec -- ex-0000000175 acquiring connection wi

In [26]:
# get result
# node data
#pgxResultSetNode = graph.query_pgql("""
#  SELECT id(x), label(x), x.FIRST_NAME, x.CITY
#  MATCH (x)-[]-()
#""")
pgxResultSetNode = graph.query_pgql("""
SELECT id_a, id_e, id_b
 FROM GRAPH_TABLE ( bank_graph
  MATCH (a) -[e]-> (b)
  COLUMNS (vertex_id(a) AS id_a, edge_id(e) AS id_e, vertex_id(b) AS id_b )
) 
""")


#['size', 'value', 'title', 'x', 'y', 'label', 'color']

node_id = []
node_title =[]
node_value = []
node_label = []

for i in pgxResultSetNode:
    size = i[0]
    if size not in node_id:
        node_id.append(size)
        node_label.append(i[1])
        if i[2] != '':
           node_title.append(i[2])
           print('Node: size: ' + str(i[0]) + ' label: ' + i[1] + ' FIRST_NAME: ' + i[2])
        elif i[3] != '':
           node_title.append(i[3])
           print('Node: size: ' + str(i[0]) + ' label: ' + i[1] + ' CITY: ' + i[3])
        else:
           node_title.append('n/a') 
           print('Node: size: ' + str(i[0]) + ' label: ' + i[1] + ' title: n/a')
        
        
        
# edge data

pgxResultSetEdge = graph.query_pgql("""
  SELECT id(x), id(y), label(e)
  MATCH (x)-[e]->(y)
""")


edge_list = []
for i in pgxResultSetEdge:
    edge_tuple = (i[0], i[1], i[2])
    edge_list.append(edge_tuple)
    print('Edge: src: ' + str(i[0]) + ' dst: ' + str(i[1]) + ' label: ' + i[2])

17:04:10.131 [main] DEBUG oracle.pgx.client.RemoteUtils -- create session cookie (session ID = e17553f2-8e88-431f-bf79-bc4cc2264a79)
17:04:10.162 [main] DEBUG oracle.pgx.client.RemoteUtils -- no value for the sticky cookie given
17:04:10.163 [main] DEBUG oracle.pgx.client.RemoteUtils -- create csrf token cookie (token = 6a2fab4b-5143-4c09-8357-2a832489cf2c)
17:04:10.163 [main] DEBUG oracle.pgx.client.HttpRequestExecutor -- Requesting POST http://graph-server.graph-oradb:7007/core/v1/pgql/run
17:04:10.164 [main] DEBUG org.apache.hc.client5.http.impl.classic.InternalHttpClient -- ex-0000000096 preparing request execution
17:04:10.164 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000096 target auth state: UNCHALLENGED
17:04:10.171 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000096 proxy auth state: UNCHALLENGED
17:04:10.176 [main] DEBUG org.apache.hc.client5.http.impl.classic.ConnectExec -- ex-0000000096 acquiring connection wi

## Open Source Vis.JS Visualization using Network Python Library

In [27]:
from pyvis.network import Network

g = Network(notebook=True, height = '800px', width = '100%' , directed = True)
g.options = {
          "nodes": {
            "scaling": {
              "min": 16,
              "max": 32,
            },
          },
          "edges": {
            "color": "GRAY",
            "smooth": "false",
          },
          "physics": {
            "barnesHut": { "gravitationalConstant": -30000 },
            "stabilization": { "iterations": 2500 },
          }
}

g.add_nodes(node_id,label=node_label,title=node_title)
g.add_edges(edge_list)
#g.show_buttons()
g.show('graph.html')

graph.html


17:04:54.936 [idle-connection-evictor-1] DEBUG org.apache.hc.client5.http.impl.io.PoolingHttpClientConnectionManager -- Closing expired connections
17:04:54.936 [idle-connection-evictor-1] DEBUG org.apache.hc.client5.http.impl.io.PoolingHttpClientConnectionManager -- Closing connections idle longer than 1 MINUTES


## OK to close session now, or skip and continue with more graphs

In [ ]:
print(session)
session.close()

## Another Vis.JS Visualization using Network Python Library

In [37]:
from pyvis.network import Network

g2 = Network(notebook=True, height = '800px', width = '100%' , directed = True)
g2.options = {
          "nodes": {
            "scaling": {
              "min": 16,
              "max": 32,
            },
          },
          "edges": {
            "color": "GRAY",
            "smooth": "false",
          },
          "physics": {
            "barnesHut": { "gravitationalConstant": -30000 },
            "stabilization": { "iterations": 2500 },
          },
          "groups": {
            "BALANCE": {
              "shape": "triangle",
              "color": "#FF9900",
            },
            "NAME": {
              "shape": "dot",
              "color": "#2B7CE9",
            },
            "ID": {
              "shape": "dot",
              "color": "#5A1E5C",
            },
          },
}

# node data
pgxResultSetNode = graph.query_pgql("""
  SELECT id(x), label(x), x.NAME, x.BALANCE
  MATCH (x)-[]-()
""")

for i in pgxResultSetNode:
    if i[2] != '':
       g2.add_node(i[0],label=i[1],group=i[1],title=i[2])
       #print('Node: size: ' + str(i[0]) + ' label: ' + i[1] + ' FIRST_NAME: ' + i[2])
    elif i[3] != '':
       g2.add_node(i[0],label=i[1],group=i[1],title=i[3])
       #print('Node: size: ' + str(i[0]) + ' label: ' + i[1] + ' CITY: ' + i[3])
    else:
       g2.add_node(i[0],label=i[1],group=i[1],title='n/a')
       #print('Node: size: ' + str(i[0]) + ' label: ' + i[1] + ' title: n/a')
        
# edge data

pgxResultSetEdge = graph.query_pgql("""
  SELECT id(x), id(y), label(e)
  MATCH (x)-[e]->(y)
""")

for i in pgxResultSetEdge:
    g2.add_edge(i[0],i[1],title=i[2])
    #print('Edge: src: ' + str(i[0]) + ' dst: ' + str(i[1]) + ' label: ' + i[2])

#g.show_buttons()
g2.show('graph2.html')

12:59:54.884 [main] DEBUG oracle.pgx.client.RemoteUtils -- create session cookie (session ID = 29e9c6bb-5d69-4d36-b42a-f4220808af5e)
12:59:54.884 [main] DEBUG oracle.pgx.client.RemoteUtils -- no value for the sticky cookie given
12:59:54.884 [main] DEBUG oracle.pgx.client.RemoteUtils -- create csrf token cookie (token = 82b380b9-951d-48e4-8f0b-8db12d32fbd8)
12:59:54.884 [main] DEBUG oracle.pgx.client.HttpRequestExecutor -- Requesting POST http://graph-server.graph-oradb:7007/core/v1/pgql/run
12:59:54.885 [main] DEBUG org.apache.hc.client5.http.impl.classic.InternalHttpClient -- ex-0000000142 preparing request execution
12:59:54.885 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000142 target auth state: UNCHALLENGED
12:59:54.885 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000142 proxy auth state: UNCHALLENGED
12:59:54.885 [main] DEBUG org.apache.hc.client5.http.impl.classic.ConnectExec -- ex-0000000142 acquiring connection wi

13:00:32.037 [idle-connection-evictor-1] DEBUG org.apache.hc.client5.http.impl.io.PoolingHttpClientConnectionManager -- Closing expired connections
13:00:32.037 [idle-connection-evictor-1] DEBUG org.apache.hc.client5.http.impl.io.PoolingHttpClientConnectionManager -- Closing connections idle longer than 1 MINUTES


## Another Vis.JS Visualization using NetworkX Python Library

In [46]:
from pyvis.network import Network
import networkx as nx

nx_graph = nx.Graph()

pgxResultSetNode = graph.query_pgql("""
  SELECT id(x), label(x), x.NAME, x.BALANCE
  MATCH (x)-[]-()
""")

for i in pgxResultSetNode:
    if i[2]:
      nx_graph.add_node(i[0], size=20, title=i[2], group=i[1])
    else:
      nx_graph.add_node(i[0], size=20, title=i[3], group=i[1])
    
# edge data
pgxResultSetEdge = graph.query_pgql("""
  SELECT id(x), id(y), label(e)
  MATCH (x)-[e]->(y)
""")

edge_list = []
for i in pgxResultSetEdge:
    nx_graph.add_edge(i[0], i[1], weight=5)
    
nt = Network(notebook=True, height = '800px', width = '100%')
# populates the nodes and edges data structures
nt.from_nx(nx_graph)
nt.show('nx.html')

16:14:21.532 [main] DEBUG oracle.pgx.client.RemoteUtils -- create session cookie (session ID = 27b7496d-4e94-43fb-8d2e-5dd1d8a4425d)
16:14:21.533 [main] DEBUG oracle.pgx.client.RemoteUtils -- no value for the sticky cookie given
16:14:21.533 [main] DEBUG oracle.pgx.client.RemoteUtils -- create csrf token cookie (token = 0ce1d5f5-989b-4999-948e-623fc4dede0a)
16:14:21.544 [main] DEBUG oracle.pgx.client.HttpRequestExecutor -- Requesting POST http://graph-server.graph-oradb:7007/core/v1/pgql/run
16:14:21.544 [main] DEBUG org.apache.hc.client5.http.impl.classic.InternalHttpClient -- ex-0000000209 preparing request execution
16:14:21.545 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000209 target auth state: UNCHALLENGED
16:14:21.545 [main] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000209 proxy auth state: UNCHALLENGED
16:14:21.545 [main] DEBUG org.apache.hc.client5.http.impl.classic.ConnectExec -- ex-0000000209 acquiring connection wi

16:14:53.073 [idle-connection-evictor-1] DEBUG org.apache.hc.client5.http.impl.io.PoolingHttpClientConnectionManager -- Closing expired connections
16:14:53.073 [idle-connection-evictor-1] DEBUG org.apache.hc.client5.http.impl.io.PoolingHttpClientConnectionManager -- Closing connections idle longer than 1 MINUTES


## Destroy Graph In PGX Memory 

In [47]:
session.destroy()

16:17:33.829 [pgx-client-thread-15] DEBUG oracle.pgx.client.RemoteCoreImpl -- Requesting DELETE http://graph-server.graph-oradb:7007/core/v1/session?_csrf_token=0ce1d5f5-989b-4999-948e-623fc4dede0a
16:17:33.842 [pgx-client-thread-15] DEBUG oracle.pgx.client.RemoteUtils -- create session cookie (session ID = 27b7496d-4e94-43fb-8d2e-5dd1d8a4425d)
16:17:33.842 [pgx-client-thread-15] DEBUG oracle.pgx.client.RemoteUtils -- no value for the sticky cookie given
16:17:33.844 [pgx-client-thread-15] DEBUG oracle.pgx.client.RemoteUtils -- create csrf token cookie (token = 0ce1d5f5-989b-4999-948e-623fc4dede0a)
16:17:33.844 [pgx-client-thread-15] DEBUG org.apache.hc.client5.http.impl.classic.InternalHttpClient -- ex-0000000238 preparing request execution
16:17:33.845 [pgx-client-thread-15] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-0000000238 target auth state: UNCHALLENGED
16:17:33.845 [pgx-client-thread-15] DEBUG org.apache.hc.client5.http.impl.classic.ProtocolExec -- ex-000